In [1]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.compose import ColumnTransformer
from sklearn.feature_extraction.text import CountVectorizer
import nltk
from nltk.stem.porter import PorterStemmer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

In [2]:
pd.set_option('display.max_columns', None)

In [3]:
df = pd.read_json('FlatData.json')

In [4]:
df.sample()

PROP_ID PROPERTY_TYPE      SOCIETY_NAME           CITY     location  \
643  X71322920          Flat  Amaya residences  Kolkata South  Narendrapur   

     BEDROOM_NUM  BALCONY_NUM  AREA  Price_per_sqft  PRICE           AGE  \
643            2            1   673            4674   0.31  Old Property   

         FURNISH amenity_luxury  FLOOR_NUM   LATITUDE  LONGITUDE  TOTAL_FLOOR  \
643  Unfurnished         Medium          1  22.426491  88.407803           14   

                                           DESCRIPTION  \
643  There is a 2 BHK apartment in Narendrapur, Kol...   

                                                 Image           Situation  \
643  https://cdn.pixabay.com/photo/2017/06/19/04/06...  Under Constraction   

    Owner_Type         Contact Facing_Direction  Loan_Availability  \
643      Owner  +91-6156710735             East              False   

     Estimated_Monthly_EMI  Maintenance_Fees  Property_Tax  \
643               36655.72              7415          9762   

     Stamp_Duty_Registration_Costs                         Nearest_Schools  \
643                            5.0  {'The Future Foundation School': 3.26}   

                        Nearest_Colleges           Nearest_Hospitals  \
643  {'Shri Shikshayatan College': 4.99}  {'Belle Vue Clinic': 7.72}   

                Nearest_Markets             Nearest_Public_Transport  \
643  {'Salt Lake Market': 2.69}  {'Mahatma Gandhi Road Metro': 9.86}   

     Nearest_Restaurants      Nearest_Railway_Stations  \
643  {'The Bridge': 6.2}  {'Tollygunge Station': 9.56}   

                      Nearest_Malls  Swimming_Pool  Playground  \
643  {'Avani Riverside Mall': 8.84}           True       False   

     RERA_Registration_Number  24x7_Security  Visitor_Parking  \
643                    270145           True            False   

     Intercom_Facility  Power_Backup Water_Supply  Pet_Friendly  \
643               True         False     Borewell          True   

     Fire_Safety_Installed  
643                   True

In [5]:
df.drop(columns=['SOCIETY_NAME','Price_per_sqft','LATITUDE','LONGITUDE'], inplace=True)

In [6]:
df.head(1)

PROP_ID PROPERTY_TYPE           CITY     location  BEDROOM_NUM  \
0  J71214794          Flat  Kolkata North  Madhyamgram            2   

   BALCONY_NUM  AREA  PRICE           AGE      FURNISH amenity_luxury  \
0            1   920   0.39  Old Property  Unfurnished         Medium   

   FLOOR_NUM  TOTAL_FLOOR                                        DESCRIPTION  \
0          1           11  Experience a new style of living with Bhawani ...   

                                               Image      Situation  \
0  https://cdn.pixabay.com/photo/2017/06/16/13/40...  Ready To Move   

  Owner_Type         Contact Facing_Direction  Loan_Availability  \
0      Owner  +91-1690606093       North-East              False   

   Estimated_Monthly_EMI  Maintenance_Fees  Property_Tax  \
0                    NaN              4698         24582   

   Stamp_Duty_Registration_Costs              Nearest_Schools  \
0                           6.57  {'St. James' School': 8.78}   

                Nearest_Colleges       Nearest_Hospitals  \
0  {'Jadavpur University': 4.44}  {'Ruby General': 6.31}   

              Nearest_Markets   Nearest_Public_Transport Nearest_Restaurants  \
0  {'Hatibagan Market': 4.64}  {'Esplanade Metro': 6.67}   {'Mocambo': 3.02}   

     Nearest_Railway_Stations         Nearest_Malls  Swimming_Pool  \
0  {'Belghoria Station': 2.2}  {'Forum Mall': 8.15}          False   

   Playground  RERA_Registration_Number  24x7_Security  Visitor_Parking  \
0        True                    904252           True             True   

   Intercom_Facility  Power_Backup Water_Supply  Pet_Friendly  \
0              False         False    Municipal         False   

   Fire_Safety_Installed  
0                  False

In [7]:
df = df.iloc[:, :14]

In [8]:
df.head()

PROP_ID PROPERTY_TYPE           CITY     location  BEDROOM_NUM  \
0  J71214794          Flat  Kolkata North  Madhyamgram            2   
1  F70835394          Flat  Kolkata South        Garia            1   
2  P69854924          Flat   Kolkata East     Rajarhat            4   
3  E69854912          Flat   Kolkata East     Rajarhat            2   
4  R69167152          Flat   Kolkata East     New Town            3   

   BALCONY_NUM  AREA  PRICE           AGE      FURNISH amenity_luxury  \
0            1   920   0.39  Old Property  Unfurnished         Medium   
1            1   535   0.27  Old Property  Unfurnished         Medium   
2            2  1940   0.92  Old Property  Unfurnished         Medium   
3            1   910   0.42  Old Property  Unfurnished         Medium   
4            1  1163   0.55  Old Property  Unfurnished         Medium   

   FLOOR_NUM  TOTAL_FLOOR                                        DESCRIPTION  
0          1           11  Experience a new style of living with Bhawani ...  
1          1            7  Let your dream of owning a flat come true with...  
2          1           20  Book your 4 BHK apartment in DTC Capital City,...  
3          1           20  Make DTC Capital City your next home. Book you...  
4          1            4  Book a spectacular property in Sai Sarovaar th...

In [9]:
def toTitle(city_name):
    return city_name.title()

In [10]:
df['CITY'] = df['CITY'].apply(toTitle)
df['location'] = df['location'].apply(toTitle)
df['AGE'] = df['AGE'].apply(toTitle)
df['FURNISH'] = df['FURNISH'].apply(toTitle)
df['amenity_luxury'] = df['amenity_luxury'].apply(toTitle)
df['DESCRIPTION'] = df['DESCRIPTION'].apply(toTitle)

In [11]:
df.head(1)

PROP_ID PROPERTY_TYPE           CITY     location  BEDROOM_NUM  \
0  J71214794          Flat  Kolkata North  Madhyamgram            2   

   BALCONY_NUM  AREA  PRICE           AGE      FURNISH amenity_luxury  \
0            1   920   0.39  Old Property  Unfurnished         Medium   

   FLOOR_NUM  TOTAL_FLOOR                                        DESCRIPTION  
0          1           11  Experience A New Style Of Living With Bhawani ...

# Structured data operation

In [226]:

categorical_features = ['location', 'AGE', 'FURNISH', 'amenity_luxury']
numerical_features = ['BEDROOM_NUM', 'BALCONY_NUM', 'AREA','PRICE']

#preprocessor = ColumnTransformer(
    #transformers=[
        #('num', StandardScaler(), numerical_features),
        #('cat', OneHotEncoder(), categorical_features)])

#structured_data = preprocessor.fit_transform(df)

ohe = OneHotEncoder(sparse=False, drop='first')
encoded_features = ohe.fit_transform(df[categorical_features])
ohe_df = pd.DataFrame(encoded_features, columns=ohe.get_feature_names_out(categorical_features))

C:\Users\dipan\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\sklearn\preprocessing\_encoders.py:972: FutureWarning: `sparse` was renamed to `sparse_output` in version 1.2 and will be removed in 1.4. `sparse_output` is ignored unless you leave `sparse` to its default value.
  warnings.warn(


In [227]:
# ohe_df

location_39/A/2, Sri Ram Thakur Road. Kolkata 700032  \
0                                                   0.0      
1                                                   0.0      
2                                                   0.0      
3                                                   0.0      
4                                                   0.0      
...                                                 ...      
5143                                                0.0      
5144                                                0.0      
5145                                                0.0      
5146                                                0.0      
5147                                                0.0      

      location_5/1B Mm Feeder Road.Kolkata-700057  location_Aa 1D Newtown  \
0                                             0.0                     0.0   
1                                             0.0                     0.0   
2                                             0.0                     0.0   
3                                             0.0                     0.0   
4                                             0.0                     0.0   
...                                           ...                     ...   
5143                                          0.0                     0.0   
5144                                          0.0                     0.0   
5145                                          0.0                     0.0   
5146                                          0.0                     0.0   
5147                                          0.0                     0.0   

      location_Action Area 1  location_Action Area 2  \
0                        0.0                     0.0   
1                        0.0                     0.0   
2                        0.0                     0.0   
3                        0.0                     0.0   
4                        0.0                     0.0   
...                      ...                     ...   
5143                     0.0                     0.0   
5144                     0.0                     0.0   
5145                     0.0                     0.0   
5146                     0.0                     0.0   
5147                     0.0                     0.0   

      location_Action Area 2 B  location_Action Area 2 New Town  \
0                          0.0                              0.0   
1                          0.0                              0.0   
2                          0.0                              0.0   
3                          0.0                              0.0   
4                          0.0                              0.0   
...                        ...                              ...   
5143                       0.0                              0.0   
5144                       0.0                              0.0   
5145                       0.0                              0.0   
5146                       0.0                              0.0   
5147                       0.0                              0.0   

      location_Action Area 2B  location_Action Area 2C  \
0                         0.0                      0.0   
1                         0.0                      0.0   
2                         0.0                      0.0   
3                         0.0                      0.0   
4                         0.0                      0.0   
...                       ...                      ...   
5143                      0.0                      0.0   
5144                      0.0                      0.0   
5145                      0.0                      0.0   
5146                      0.0                      0.0   
5147                      0.0                      0.0   

      location_Action Area 3  location_Agarpara  location_Airport  \
0                        0.0                0.0               0.0   
1                      

In [228]:
df_final_with_ohe = pd.concat([df.drop(columns=categorical_features), ohe_df], axis=1)

In [229]:
#df_final_with_ohe

PROP_ID PROPERTY_TYPE           CITY  BEDROOM_NUM  BALCONY_NUM  AREA  \
0     J71214794          Flat  Kolkata North            2            1   920   
1     F70835394          Flat  Kolkata South            1            1   535   
2     P69854924          Flat   Kolkata East            4            2  1940   
3     E69854912          Flat   Kolkata East            2            1   910   
4     R69167152          Flat   Kolkata East            3            1  1163   
...         ...           ...            ...          ...          ...   ...   
5143  U71217472          Flat  Kolkata South            2            1   730   
5144  E64737128          Flat  Kolkata South            3            1  2000   
5145  J66826540          Flat  Kolkata South            3            2  1843   
5146  E66826562          Flat  Kolkata South            3            2  2079   
5147  J71210104          Flat   Kolkata East            2            1  1257   

      PRICE  FLOOR_NUM  TOTAL_FLOOR  \
0      0.39          1           11   
1      0.27          1            7   
2      0.92          1           20   
3      0.42          1           20   
4      0.55          1            4   
...     ...        ...          ...   
5143   0.33          2            2   
5144   1.80          2            5   
5145   1.55         14           19   
5146   1.75         10           19   
5147   0.74          3           17   

                                            DESCRIPTION  \
0     Experience A New Style Of Living With Bhawani ...   
1     Let Your Dream Of Owning A Flat Come True With...   
2     Book Your 4 Bhk Apartment In Dtc Capital City,...   
3     Make Dtc Capital City Your Next Home. Book You...   
4     Book A Spectacular Property In Sai Sarovaar Th...   
...                                                 ...   
5143  There Is No Brokerage Charges For This Propert...   
5144  This Beautiful 3 Bhk Flat In New Alipore, Kolk...   
5145  Ambuja Upohar The Condoville Is One Of The Mos...   
5146  Looking For A 3 Bhk Property For Sale In Kolka...   
5147  It Is A Standard 2 Bhk With 2 Room, 2 Bath, 1 ...   

      location_39/A/2, Sri Ram Thakur Road. Kolkata 700032  \
0                                                   0.0      
1                                                   0.0      
2                                                   0.0      
3                                                   0.0      
4                                                   0.0      
...                                                 ...      
5143                                                0.0      
5144                                                0.0      
5145                                                0.0      
5146                                                0.0      
5147                                                0.0      

      location_5/1B Mm Feeder Road.Kolkata-700057  location_Aa 1D Newtown  \
0                                             0.0                     0.0   
1                                             0.0                     0.0   
2                                             0.0                     0.0   
3                                             0.0                     0.0   
4                                             0.0                     0.0   
...                                           ...                     ...   
5143                                          0.0                     0.0   
5144                                          0.0                     0.0   
5145                                          0.0                     0.0   
5146                                          0.0                     0.0   
5147                                          0.0                     0.0   

      location_Action Area 1  location_Action Area 2  \
0                        0.0                     0.0   
1                        0.0                     0.0   
2                        0.0   

In [248]:

scaler = StandardScaler()

# Fit and transform the numerical features
df_final_with_ohe[numerical_features] = scaler.fit_transform(df_final_with_ohe[numerical_features])

# Main Df

In [258]:
df_final_with_ohe.head(1)

PROP_ID PROPERTY_TYPE           CITY  BEDROOM_NUM  BALCONY_NUM      AREA  \
0  J71214794          Flat  Kolkata North    -0.820708    -0.393227 -0.507156   

      PRICE  FLOOR_NUM  TOTAL_FLOOR  \
0 -0.497435          1           11   

                                         DESCRIPTION  \
0  experi a new style of live with bhawani bandha...   

   location_39/A/2, Sri Ram Thakur Road. Kolkata 700032  \
0                                                0.0      

   location_5/1B Mm Feeder Road.Kolkata-700057  location_Aa 1D Newtown  \
0                                          0.0                     0.0   

   location_Action Area 1  location_Action Area 2  location_Action Area 2 B  \
0                     0.0                     0.0                       0.0   

   location_Action Area 2 New Town  location_Action Area 2B  \
0                              0.0                      0.0   

   location_Action Area 2C  location_Action Area 3  location_Agarpara  \
0                      0.0                     0.0                0.0   

   location_Airport  location_Ajc Bose Road  location_Ajoy Nagar  \
0               0.0                     0.0                  0.0   

   location_Alipore  location_Amarpalli  \
0               0.0                 0.0   

   location_Ambuja Udita, Survey Park,Santoshpur  location_Amrabati  \
0                                            0.0                0.0   

   location_Amtala  location_Anandapur  location_Anandapuri  location_Ananya  \
0              0.0                 0.0                  0.0              0.0   

   location_Andul Road  location_Arabinda Pally  location_Ariadaha  \
0                  0.0                      0.0                0.0   

   location_Ashok Nagar  location_Atghara  location_Atlas More, Narendrapur  \
0                   0.0               0.0                               0.0   

   location_Auckland Square  location_Azadgarh  location_Bablatala  \
0                       0.0                0.0                 0.0   

   location_Badam Talla  location_Badamtala  location_Bagha Jatin  \
0                   0.0                 0.0                   0.0   

   location_Baghajatin Place  location_Baguiati  location_Baguihati  \
0                        0.0                0.0                 0.0   

   location_Baguihati Jyangra  location_Baishnabghata  \
0                         0.0                     0.0   

   location_Baishnabghata Bye Lane  location_Bakul Bagan  location_Bakultala  \
0                              0.0                   0.0                 0.0   

   location_Bally  location_Ballygunge  location_Ballygunge Circular Road  \
0             0.0                  0.0                                0.0   

   location_Ballygunge Gardens  location_Ballygunge Place  location_Bandel  \
0                          0.0                        0.0              0.0   

   location_Bangur  location_Bangur Avenue  location_Bansdroni  \
0              0.0                     0.0                 0.0   

   location_Bansdroni Park  location_Bara Nagar  location_Barasat  \
0                      0.0                  0.0               0.0   

   location_Barat Colony  location_Barhans  location_Barrackpore  \
0                    0.0               0.0                   0.0   

   location_Baruipur  location_Basunagar  location_Batanagar  \
0                0.0                 0.0                 0.0   

   location_Bd Block  location_Be... Block  location_Behala  \
0                0.0                   0.0              0.0   

   location_Behala Chowrasta  location_Behala Manton  \
0                        0.0                     0.0   

   location_Behala Shakuntala Park  location_Behala Thana  \
0                              0.0                    0.0   

   location_Behala Unique Park  location_Beleghata  location_Belgachia  \
0                          0.0                 0.0                 0.0   

   location_Belgharia  location_Beliaghata  location_Belur  

In [252]:
df = df_final_with_ohe

In [254]:
# df.head()

PROP_ID PROPERTY_TYPE           CITY  BEDROOM_NUM  BALCONY_NUM      AREA  \
0  J71214794          Flat  Kolkata North    -0.820708    -0.393227 -0.507156   
1  F70835394          Flat  Kolkata South    -2.142261    -0.393227 -1.135731   
2  P69854924          Flat   Kolkata East     1.822398     1.377843  1.158161   
3  E69854912          Flat   Kolkata East    -0.820708    -0.393227 -0.523482   
4  R69167152          Flat   Kolkata East     0.500845    -0.393227 -0.110418   

      PRICE  FLOOR_NUM  TOTAL_FLOOR  \
0 -0.497435          1           11   
1 -0.622327          1            7   
2  0.054169          1           20   
3 -0.466212          1           20   
4 -0.330913          1            4   

                                         DESCRIPTION  \
0  experi a new style of live with bhawani bandha...   
1  let your dream of own a flat come true with ga...   
2  book your 4 bhk apart in dtc capit city, rajar...   
3  make dtc capit citi your next home. book your ...   
4  book a spectacular properti in sai sarovaar th...   

   location_39/A/2, Sri Ram Thakur Road. Kolkata 700032  \
0                                                0.0      
1                                                0.0      
2                                                0.0      
3                                                0.0      
4                                                0.0      

   location_5/1B Mm Feeder Road.Kolkata-700057  location_Aa 1D Newtown  \
0                                          0.0                     0.0   
1                                          0.0                     0.0   
2                                          0.0                     0.0   
3                                          0.0                     0.0   
4                                          0.0                     0.0   

   location_Action Area 1  location_Action Area 2  location_Action Area 2 B  \
0                     0.0                     0.0                       0.0   
1                     0.0                     0.0                       0.0   
2                     0.0                     0.0                       0.0   
3                     0.0                     0.0                       0.0   
4                     0.0                     0.0                       0.0   

   location_Action Area 2 New Town  location_Action Area 2B  \
0                              0.0                      0.0   
1                              0.0                      0.0   
2                              0.0                      0.0   
3                              0.0                      0.0   
4                              0.0                      0.0   

   location_Action Area 2C  location_Action Area 3  location_Agarpara  \
0                      0.0                     0.0                0.0   
1                      0.0                     0.0                0.0   
2                      0.0                     0.0                0.0   
3                      0.0                     0.0                0.0   
4                      0.0                     0.0                0.0   

   location_Airport  location_Ajc Bose Road  location_Ajoy Nagar  \
0               0.0                     0.0                  0.0   
1               0.0                     0.0                  0.0   
2               0.0                     0.0                  0.0   
3               0.0                     0.0                  0.0   
4               0.0                     0.0                  0.0   

   location_Alipore  location_Amarpalli  \
0               0.0                 0.0   
1               0.0                 0.0   
2               0.0                 0.0   
3               0.0                 0.0   
4               0.0                 0.0   

   location_Ambuja Udita, Survey Park,Santoshpur  location_Amrabati  \
0                                            0.0                0.0   
1                                          

# Description Operation

In [255]:
ps = PorterStemmer()

In [259]:
def stem(text):
    y = []
    for i in text.split():
        y.append(ps.stem(i))
    return " ".join(y)

In [260]:
df['DESCRIPTION']=df['DESCRIPTION'].apply(stem)

In [261]:


# Initialize the TF-IDF vectorizer
tfidf_vectorizer = TfidfVectorizer(max_features=5000, stop_words='english')

# Fit and transform the description column
vectors = tfidf_vectorizer.fit_transform(df['DESCRIPTION'])

description_df = pd.DataFrame(vectors.toarray(), index=df.index)

In [262]:
#ndescription_df

0     1     2     3     4     5     6     7     8     9     10    11    \
0      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
2      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
3      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
4      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
5143   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5144   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5145   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5146   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5147   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   

      12        13    14    15    16    17    18    19    20    21    22    \
0      0.0  0.000000   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1      0.0  0.000000   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
2      0.0  0.000000   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
3      0.0  0.000000   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
4      0.0  0.000000   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
...    ...       ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
5143   0.0  0.000000   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5144   0.0  0.161024   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5145   0.0  0.129787   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5146   0.0  0.136068   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5147   0.0  0.000000   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   

      23    24    25    26    27    28    29    30    31    32    33    34    \
0      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
2      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
3      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
4      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
5143   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5144   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5145   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5146   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5147   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   

      35    36    37    38    39    40    41    42    43    44    45    46    \
0      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
2      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
3      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
4      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
5143   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5144   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5145   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5146   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
5147   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   

      47    48    49    50    51    52    53    54    55    56    57    58    \
0      0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   0.0   
1      0.0   0.0   0.0   0

In [309]:
# df

PROP_ID PROPERTY_TYPE           CITY  BEDROOM_NUM  BALCONY_NUM  \
0     J71214794          Flat  Kolkata North    -0.820708    -0.393227   
1     F70835394          Flat  Kolkata South    -2.142261    -0.393227   
2     P69854924          Flat   Kolkata East     1.822398     1.377843   
3     E69854912          Flat   Kolkata East    -0.820708    -0.393227   
4     R69167152          Flat   Kolkata East     0.500845    -0.393227   
...         ...           ...            ...          ...          ...   
5143  U71217472          Flat  Kolkata South    -0.820708    -0.393227   
5144  E64737128          Flat  Kolkata South     0.500845    -0.393227   
5145  J66826540          Flat  Kolkata South     0.500845     1.377843   
5146  E66826562          Flat  Kolkata South     0.500845     1.377843   
5147  J71210104          Flat   Kolkata East    -0.820708    -0.393227   

          AREA     PRICE  FLOOR_NUM  TOTAL_FLOOR  \
0    -0.507156 -0.497435          1           11   
1    -1.135731 -0.622327          1            7   
2     1.158161  0.054169          1           20   
3    -0.523482 -0.466212          1           20   
4    -0.110418 -0.330913          1            4   
...        ...       ...        ...          ...   
5143 -0.817362 -0.559881          2            2   
5144  1.256120  0.970040          2            5   
5145  0.999792  0.709850         14           19   
5146  1.385101  0.918002         10           19   
5147  0.043052 -0.133168          3           17   

                                            DESCRIPTION  \
0     experi a new style of live with bhawani bandha...   
1     let your dream of own a flat come true with ga...   
2     book your 4 bhk apart in dtc capit city, rajar...   
3     make dtc capit citi your next home. book your ...   
4     book a spectacular properti in sai sarovaar th...   
...                                                 ...   
5143  there is no brokerag charg for thi properti pr...   
5144  thi beauti 3 bhk flat in new alipore, kolkata ...   
5145  ambuja upohar the condovil is one of the most ...   
5146  look for a 3 bhk properti for sale in kolkata ...   
5147  it is a standard 2 bhk with 2 room, 2 bath, 1 ...   

      location_39/A/2, Sri Ram Thakur Road. Kolkata 700032  \
0                                                   0.0      
1                                                   0.0      
2                                                   0.0      
3                                                   0.0      
4                                                   0.0      
...                                                 ...      
5143                                                0.0      
5144                                                0.0      
5145                                                0.0      
5146                                                0.0      
5147                                                0.0      

      location_5/1B Mm Feeder Road.Kolkata-700057  location_Aa 1D Newtown  \
0                                             0.0                     0.0   
1                                             0.0                     0.0   
2                                             0.0                     0.0   
3                                             0.0                     0.0   
4                                             0.0                     0.0   
...                                           ...                     ...   
5143                                          0.0                     0.0   
5144                                          0.0                     0.0   
5145                                          0.0                     0.0   
5146                                          0.0                     0.0   
5147                                          0.0                     0.0   

      location_Action Area 1  location_Action Area 2  \
0                        0.0                     0.0   
1  

In [310]:
final_df = pd.concat([df,description_df], axis=1)

In [300]:
final_df.head(1)

PROP_ID PROPERTY_TYPE           CITY  BEDROOM_NUM  BALCONY_NUM      AREA  \
0  J71214794          Flat  Kolkata North    -0.820708    -0.393227 -0.507156   

      PRICE  FLOOR_NUM  TOTAL_FLOOR  \
0 -0.497435          1           11   

                                         DESCRIPTION  \
0  experi a new style of live with bhawani bandha...   

   location_39/A/2, Sri Ram Thakur Road. Kolkata 700032  \
0                                                0.0      

   location_5/1B Mm Feeder Road.Kolkata-700057  location_Aa 1D Newtown  \
0                                          0.0                     0.0   

   location_Action Area 1  location_Action Area 2  location_Action Area 2 B  \
0                     0.0                     0.0                       0.0   

   location_Action Area 2 New Town  location_Action Area 2B  \
0                              0.0                      0.0   

   location_Action Area 2C  location_Action Area 3  location_Agarpara  \
0                      0.0                     0.0                0.0   

   location_Airport  location_Ajc Bose Road  location_Ajoy Nagar  \
0               0.0                     0.0                  0.0   

   location_Alipore  location_Amarpalli  \
0               0.0                 0.0   

   location_Ambuja Udita, Survey Park,Santoshpur  location_Amrabati  \
0                                            0.0                0.0   

   location_Amtala  location_Anandapur  location_Anandapuri  location_Ananya  \
0              0.0                 0.0                  0.0              0.0   

   location_Andul Road  location_Arabinda Pally  location_Ariadaha  \
0                  0.0                      0.0                0.0   

   location_Ashok Nagar  location_Atghara  location_Atlas More, Narendrapur  \
0                   0.0               0.0                               0.0   

   location_Auckland Square  location_Azadgarh  location_Bablatala  \
0                       0.0                0.0                 0.0   

   location_Badam Talla  location_Badamtala  location_Bagha Jatin  \
0                   0.0                 0.0                   0.0   

   location_Baghajatin Place  location_Baguiati  location_Baguihati  \
0                        0.0                0.0                 0.0   

   location_Baguihati Jyangra  location_Baishnabghata  \
0                         0.0                     0.0   

   location_Baishnabghata Bye Lane  location_Bakul Bagan  location_Bakultala  \
0                              0.0                   0.0                 0.0   

   location_Bally  location_Ballygunge  location_Ballygunge Circular Road  \
0             0.0                  0.0                                0.0   

   location_Ballygunge Gardens  location_Ballygunge Place  location_Bandel  \
0                          0.0                        0.0              0.0   

   location_Bangur  location_Bangur Avenue  location_Bansdroni  \
0              0.0                     0.0                 0.0   

   location_Bansdroni Park  location_Bara Nagar  location_Barasat  \
0                      0.0                  0.0               0.0   

   location_Barat Colony  location_Barhans  location_Barrackpore  \
0                    0.0               0.0                   0.0   

   location_Baruipur  location_Basunagar  location_Batanagar  \
0                0.0                 0.0                 0.0   

   location_Bd Block  location_Be... Block  location_Behala  \
0                0.0                   0.0              0.0   

   location_Behala Chowrasta  location_Behala Manton  \
0                        0.0                     0.0   

   location_Behala Shakuntala Park  location_Behala Thana  \
0                              0.0                    0.0   

   location_Behala Unique Park  location_Beleghata  location_Belgachia  \
0                          0.0                 0.0                 0.0   

   location_Belgharia  location_Beliaghata  location_Belur  

In [311]:
final_df.drop(columns =['PROPERTY_TYPE','CITY','DESCRIPTION','FLOOR_NUM','TOTAL_FLOOR'],inplace = True)

In [305]:
#final_df.set_index('PROP_ID', inplace=True)

In [306]:
# final_df

BEDROOM_NUM  BALCONY_NUM      AREA     PRICE  \
PROP_ID                                                   
J71214794    -0.820708    -0.393227 -0.507156 -0.497435   
F70835394    -2.142261    -0.393227 -1.135731 -0.622327   
P69854924     1.822398     1.377843  1.158161  0.054169   
E69854912    -0.820708    -0.393227 -0.523482 -0.466212   
R69167152     0.500845    -0.393227 -0.110418 -0.330913   
...                ...          ...       ...       ...   
U71217472    -0.820708    -0.393227 -0.817362 -0.559881   
E64737128     0.500845    -0.393227  1.256120  0.970040   
J66826540     0.500845     1.377843  0.999792  0.709850   
E66826562     0.500845     1.377843  1.385101  0.918002   
J71210104    -0.820708    -0.393227  0.043052 -0.133168   

           location_39/A/2, Sri Ram Thakur Road. Kolkata 700032  \
PROP_ID                                                           
J71214794                                                0.0      
F70835394                                                0.0      
P69854924                                                0.0      
E69854912                                                0.0      
R69167152                                                0.0      
...                                                      ...      
U71217472                                                0.0      
E64737128                                                0.0      
J66826540                                                0.0      
E66826562                                                0.0      
J71210104                                                0.0      

           location_5/1B Mm Feeder Road.Kolkata-700057  \
PROP_ID                                                  
J71214794                                          0.0   
F70835394                                          0.0   
P69854924                                          0.0   
E69854912                                          0.0   
R69167152                                          0.0   
...                                                ...   
U71217472                                          0.0   
E64737128                                          0.0   
J66826540                                          0.0   
E66826562                                          0.0   
J71210104                                          0.0   

           location_Aa 1D Newtown  location_Action Area 1  \
PROP_ID                                                     
J71214794                     0.0                     0.0   
F70835394                     0.0                     0.0   
P69854924                     0.0                     0.0   
E69854912                     0.0                     0.0   
R69167152                     0.0                     0.0   
...                           ...                     ...   
U71217472                     0.0                     0.0   
E64737128                     0.0                     0.0   
J66826540                     0.0                     0.0   
E66826562                     0.0                     0.0   
J71210104                     0.0                     0.0   

           location_Action Area 2  location_Action Area 2 B  \
PROP_ID                                                       
J71214794                     0.0                       0.0   
F70835394                     0.0                       0.0   
P69854924                     0.0                       0.0   
E69854912                     0.0                       0.0   
R69167152                     0.0                       0.0   
...                           ...                       ...   
U71217472                     0.0                       0.0   
E64737128                     0.0                       0.0   
J66826540                     0.0                       0.0   
E66826562                     0.0                       0.0   
J71210104                     0.0                       0.0   

  

In [284]:
#final_df.to_csv('Encoded_data.csv', index = False)

In [313]:
final_df.drop(columns = ['PROP_ID'], inplace = True)
features = final_df.values  

similarity_matrix = cosine_similarity(features)

In [308]:
similarity_matrix

array([[ 1.        ,  0.70637744,  0.06165166, ..., -0.23869634,
        -0.26088982,  0.18315728],
       [ 0.70637744,  1.        , -0.23699466, ..., -0.31485219,
        -0.34783279,  0.29694678],
       [ 0.06165166, -0.23699466,  1.        , ...,  0.40508085,
         0.42291918, -0.29668328],
       ...,
       [-0.23869634, -0.31485219,  0.40508085, ...,  1.        ,
         0.95798727,  0.00959094],
       [-0.26088982, -0.34783279,  0.42291918, ...,  0.95798727,
         1.        ,  0.00589459],
       [ 0.18315728,  0.29694678, -0.29668328, ...,  0.00959094,
         0.00589459,  1.        ]])

In [320]:
similarity_matrix[0]

array([ 1.        ,  0.70637744,  0.06165166, ..., -0.23869634,
       -0.26088982,  0.18315728])

In [323]:
sorted(similarity_matrix[2], reverse=True)

[0.9999999999999999,
 0.9617484581608523,
 0.9489521556899063,
 0.9484885442373151,
 0.9475419703032045,
 0.9467952423906177,
 0.9459510007970015,
 0.9456259622186599,
 0.945034828710044,
 0.9436476963896147,
 0.9435487856344015,
 0.8796008979795654,
 0.8677465965210767,
 0.8637874501940219,
 0.8612859413617511,
 0.8518436695042069,
 0.848311612333128,
 0.8458673150093643,
 0.8430487764574623,
 0.8426383180529662,
 0.8401467334177983,
 0.8371933814837117,
 0.8355663771836638,
 0.8344882549098176,
 0.8334171044365604,
 0.8332144647194563,
 0.8315861720838422,
 0.8315610191537157,
 0.8295191998345822,
 0.829145996889951,
 0.8288313125084719,
 0.8285771809845872,
 0.8280116194254938,
 0.8263291963653855,
 0.8250464128015634,
 0.8245908251050557,
 0.8228681284734033,
 0.8223402958453907,
 0.8218793736927053,
 0.8218337250935309,
 0.8203892086576525,
 0.8195817237061107,
 0.8183501489025079,
 0.8180945575069855,
 0.8156244177945081,
 0.8154422478536596,
 0.8153129567625211,
 0.8145484852305

In [319]:
df[df['PROP_ID'] == 'F70835394'].index[0]

1

In [329]:
sorted(list(enumerate(similarity_matrix[0])),reverse=True, key= lambda x: x[1])[1:6]

[(21, 0.8818335549631755),
 (672, 0.8806265960401265),
 (830, 0.8796757041587837),
 (16, 0.8792002313112052),
 (788, 0.8757665811532289)]

In [13]:
import pickle
import pandas as pd
import numpy as np
from django.http import JsonResponse



with open('./similarity.pkl', 'rb') as file1:
    similarity = pickle.load(file1)
with open('./prediction_df.pkl', 'rb') as file2:
    df = pickle.load(file2)

In [16]:


def recommended(PROP_ID):
  
    try:
        prop_index = df[df['PROP_ID'] == PROP_ID].index[0]
    except IndexError:
        return JsonResponse({'error': 'Property not found'}, status=404)

    distances = similarity[prop_index]
    property_list = sorted(list(enumerate(distances)), reverse=True, key=lambda x: x[1])[1:11]

    recommended_properties = []
    for index, distance in property_list:
        recommended_properties.append({
            'PropertyID': df.iloc[index]['PROP_ID'],
            'Similarity': f"{distance * 100:.2f}%"  
        })

    return JsonResponse(recommended_properties, safe=False)


In [349]:
df.sample()

PROP_ID PROPERTY_TYPE          CITY  BEDROOM_NUM  BALCONY_NUM  \
4204  I71000594          Flat  Kolkata East    -0.820708    -0.393227   

          AREA     PRICE  FLOOR_NUM  TOTAL_FLOOR  \
4204 -0.575727 -0.611919          5            5   

                                            DESCRIPTION  \
4204  thi 2 bhk apart is avail for sale in ideal aba...   

      location_39/A/2, Sri Ram Thakur Road. Kolkata 700032  \
4204                                                0.0      

      location_5/1B Mm Feeder Road.Kolkata-700057  location_Aa 1D Newtown  \
4204                                          0.0                     0.0   

      location_Action Area 1  location_Action Area 2  \
4204                     0.0                     0.0   

      location_Action Area 2 B  location_Action Area 2 New Town  \
4204                       0.0                              0.0   

      location_Action Area 2B  location_Action Area 2C  \
4204                      0.0                      0.0   

      location_Action Area 3  location_Agarpara  location_Airport  \
4204                     0.0                0.0               0.0   

      location_Ajc Bose Road  location_Ajoy Nagar  location_Alipore  \
4204                     0.0                  0.0               0.0   

      location_Amarpalli  location_Ambuja Udita, Survey Park,Santoshpur  \
4204                 0.0                                            0.0   

      location_Amrabati  location_Amtala  location_Anandapur  \
4204                0.0              0.0                 0.0   

      location_Anandapuri  location_Ananya  location_Andul Road  \
4204                  0.0              0.0                  0.0   

      location_Arabinda Pally  location_Ariadaha  location_Ashok Nagar  \
4204                      0.0                0.0                   0.0   

      location_Atghara  location_Atlas More, Narendrapur  \
4204               0.0                               0.0   

      location_Auckland Square  location_Azadgarh  location_Bablatala  \
4204                       0.0                0.0                 0.0   

      location_Badam Talla  location_Badamtala  location_Bagha Jatin  \
4204                   0.0                 0.0                   0.0   

      location_Baghajatin Place  location_Baguiati  location_Baguihati  \
4204                        0.0                0.0                 0.0   

      location_Baguihati Jyangra  location_Baishnabghata  \
4204                         0.0                     0.0   

      location_Baishnabghata Bye Lane  location_Bakul Bagan  \
4204                              0.0                   0.0   

      location_Bakultala  location_Bally  location_Ballygunge  \
4204                 0.0             0.0                  0.0   

      location_Ballygunge Circular Road  location_Ballygunge Gardens  \
4204                                0.0                          0.0   

      location_Ballygunge Place  location_Bandel  location_Bangur  \
4204                        0.0              0.0              0.0   

      location_Bangur Avenue  location_Bansdroni  location_Bansdroni Park  \
4204                     0.0                 0.0                      0.0   

      location_Bara Nagar  location_Barasat  location_Barat Colony  \
4204                  0.0               0.0                    0.0   

      location_Barhans  location_Barrackpore  location_Baruipur  \
4204               0.0                   0.0                0.0   

      location_Basunagar  location_Batanagar  location_Bd Block  \
4204                 0.0                 0.0                0.0   

      location_Be... Block  location_Behala  location_Behala Chowrasta  \
4204                   0.0              0.0                        0.0   

      location_Behala Manton  location_Behala Shakuntala Park  \
4204                     0.0                              0.0   

      location_Behala Thana  location_Behala Unique Park  location_Beleghat

In [ ]:
recommended('I71000594')

Property ID: Y70893286, Similarity: 94.70%
Property ID: L70906528, Similarity: 94.29%
Property ID: X70940390, Similarity: 93.93%
Property ID: C70906422, Similarity: 93.55%
Property ID: N70893010, Similarity: 92.75%
Property ID: W70910084, Similarity: 92.73%
Property ID: D69231308, Similarity: 91.50%
Property ID: R68481550, Similarity: 91.26%
Property ID: C70895162, Similarity: 91.06%
Property ID: Z68916300, Similarity: 90.69%


In [351]:

#pickle.dump(similarity_matrix,open('similarity.pkl','wb'))

In [18]:
#pickle.dump(df,open('prediction_df.pkl','wb'))

# Recommendation system based on prediction:

In [28]:
df = pd.read_json('FlatData.json')

In [29]:
df.head(1)

PROP_ID PROPERTY_TYPE     SOCIETY_NAME           CITY     location  \
0  J71214794          Flat  Bhawani bandhan  Kolkata North  Madhyamgram   

   BEDROOM_NUM  BALCONY_NUM  AREA  Price_per_sqft  PRICE           AGE  \
0            2            1   920            4239   0.39  Old Property   

       FURNISH amenity_luxury  FLOOR_NUM   LATITUDE  LONGITUDE  TOTAL_FLOOR  \
0  Unfurnished         Medium          1  22.690003   88.45908           11   

                                         DESCRIPTION  \
0  Experience a new style of living with Bhawani ...   

                                               Image      Situation  \
0  https://cdn.pixabay.com/photo/2017/06/16/13/40...  Ready To Move   

  Owner_Type         Contact Facing_Direction  Loan_Availability  \
0      Owner  +91-1690606093       North-East              False   

   Estimated_Monthly_EMI  Maintenance_Fees  Property_Tax  \
0                    NaN              4698         24582   

   Stamp_Duty_Registration_Costs              Nearest_Schools  \
0                           6.57  {'St. James' School': 8.78}   

                Nearest_Colleges       Nearest_Hospitals  \
0  {'Jadavpur University': 4.44}  {'Ruby General': 6.31}   

              Nearest_Markets   Nearest_Public_Transport Nearest_Restaurants  \
0  {'Hatibagan Market': 4.64}  {'Esplanade Metro': 6.67}   {'Mocambo': 3.02}   

     Nearest_Railway_Stations         Nearest_Malls  Swimming_Pool  \
0  {'Belghoria Station': 2.2}  {'Forum Mall': 8.15}          False   

   Playground  RERA_Registration_Number  24x7_Security  Visitor_Parking  \
0        True                    904252           True             True   

   Intercom_Facility  Power_Backup Water_Supply  Pet_Friendly  \
0              False         False    Municipal         False   

   Fire_Safety_Installed  
0                  False

In [ ]:
# location, bedroom no, builtud area, balcony, age, furnish, amenity,floor,price

In [30]:
dfData = df[['PROP_ID','location','BEDROOM_NUM','AREA','BALCONY_NUM','AGE','FURNISH','amenity_luxury','PRICE']]

In [31]:
dfData

PROP_ID     location  BEDROOM_NUM  AREA  BALCONY_NUM  \
0     J71214794  Madhyamgram            2   920            1   
1     F70835394        Garia            1   535            1   
2     P69854924     Rajarhat            4  1940            2   
3     E69854912     Rajarhat            2   910            1   
4     R69167152     New Town            3  1163            1   
...         ...          ...          ...   ...          ...   
5143  U71217472       Behala            2   730            1   
5144  E64737128  New Alipore            3  2000            1   
5145  J66826540   Chak Garia            3  1843            2   
5146  E66826562   Chak Garia            3  2079            2   
5147  J71210104     New Town            2  1257            1   

                          AGE           FURNISH amenity_luxury  PRICE  
0                Old Property       Unfurnished         Medium   0.39  
1                Old Property       Unfurnished         Medium   0.27  
2                Old Property       Unfurnished         Medium   0.92  
3                Old Property       Unfurnished         Medium   0.42  
4                Old Property       Unfurnished         Medium   0.55  
...                       ...               ...            ...    ...  
5143  Relatively New Property   Fully furnished         Medium   0.33  
5144           Moderately Old  Luxury furnished            Low   1.80  
5145             New Property  Luxury furnished            Low   1.55  
5146             New Property  Luxury furnished            Low   1.75  
5147             New Property   Fully furnished           High   0.74  

[5148 rows x 9 columns]

In [16]:
df = df[['location','BEDROOM_NUM','AREA','BALCONY_NUM','AGE','FURNISH','amenity_luxury','PRICE']]

In [20]:
df[df['BEDROOM_NUM']==2]

location  BEDROOM_NUM  AREA  BALCONY_NUM                      AGE  \
0     Madhyamgram            2   920            1             Old Property   
3        Rajarhat            2   910            1             Old Property   
5        New Town            2   901            1             Old Property   
6         Bt Road            2   732            1             Old Property   
8        New Town            2  1050            1             Old Property   
...           ...          ...   ...          ...                      ...   
5138      Sodepur            2   715            1  Relatively New Property   
5141      Sodepur            2   710            1  Relatively New Property   
5142      Bt Road            2  1100            1             Old Property   
5143       Behala            2   730            1  Relatively New Property   
5147     New Town            2  1257            1             New Property   

              FURNISH amenity_luxury  PRICE  
0         Unfurnished         Medium   0.39  
3         Unfurnished         Medium   0.42  
5         Unfurnished         Medium   0.42  
6         Unfurnished         Medium   0.64  
8         Unfurnished         Medium   0.55  
...               ...            ...    ...  
5138      Unfurnished         Medium   0.21  
5141  Fully Furnished         Medium   0.21  
5142  Fully Furnished           High   0.66  
5143  Fully Furnished         Medium   0.33  
5147  Fully Furnished           High   0.74  

[2111 rows x 8 columns]

In [18]:
categorical_columns = ['location','AGE','FURNISH','amenity_luxury']
numerial_columns = ['BEDROOM_NUM','AREA','BALCONY_NUM','PRICE'] 

In [ ]:
prediction_recommendation(2, )

In [25]:
import pandas as pd
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.compose import ColumnTransformer
from sklearn.metrics.pairwise import cosine_similarity

def prediction_recommendation(df, BEDROOM_NUM=None, location=None, AGE=None, FURNISH=None, 
                              amenity_luxury=None, AREA=None, BALCONY_NUM=None, PRICE=None, top_n=5):
    
    # User input data
    new_data = {
        'BEDROOM_NUM': [BEDROOM_NUM],
        'location': [location],
        'AGE': [AGE],
        'FURNISH': [FURNISH],
        'amenity_luxury': [amenity_luxury],
        'AREA': [AREA],
        'BALCONY_NUM': [BALCONY_NUM],
        'PRICE': [PRICE]
    }
    new_df = pd.DataFrame(new_data)
    
    # Columns to process
    categorical_columns = ['location', 'AGE', 'FURNISH', 'amenity_luxury']
    numerical_columns = ['BEDROOM_NUM', 'AREA', 'BALCONY_NUM', 'PRICE']
    
    # Preprocessing: OneHot for categorical, StandardScaler for numerical
    preprocessor = ColumnTransformer(
        transformers=[
            ('cat', OneHotEncoder(), categorical_columns),
            ('num', StandardScaler(), numerical_columns)
        ])
    
    # Fit on the existing dataset without the new input
    processed_existing_data = preprocessor.fit_transform(df)
    
    # Transform the new data
    processed_new_data = preprocessor.transform(new_df)
    
    # Calculate cosine similarity between the new property and all existing properties
    similarity_scores = cosine_similarity(processed_new_data, processed_existing_data)
    
    # Get top N recommendations based on similarity scores
    top_n_indices = similarity_scores.argsort()[0][-top_n:][::-1]
    top_n_scores = similarity_scores[0][top_n_indices]
    
    # Combine indices and scores into tuples
    recommendations = list(zip(top_n_indices, top_n_scores))
    
    return recommendations

# Example usage
# Assuming `df` is your original dataset with historical real estate data
recommendations = prediction_recommendation(df, BEDROOM_NUM=3, location="New Town", AGE="Old Property", 
                                            FURNISH="Fully Furnished", amenity_luxury="High", 
                                            AREA=1200, BALCONY_NUM=2, PRICE=.89)

print("Recommendations:", recommendations)


Recommendations: [(2123, 0.9817350318275218), (5061, 0.9762101764949189), (4662, 0.9444902846626533), (5067, 0.8621320262203198), (2210, 0.8612343551665221)]


In [32]:
# import pickle
#pickle.dump(dfData,open('df_prediction_recommendation.pkl','wb'))